Example: Running breakdown voltage model validation.

This script demonstrates how to use the validation module to compare
breakdown voltage models against experimental data.


In [ ]:
import numpy as np
import openmdao.api as om

from paroto.models.breakdown_voltage import (
    PaschenSimpleModel,
    PaschenTemperatureCorrectedModel,
    RepetitivePulseBreakdownModel,
)
from paroto.validation.experimental_data import (
    get_gs_transition_data,
    get_paschen_curve_air,
)

print("=" * 70)
print("Breakdown Voltage Model Validation Example")
print("=" * 70)

# Example 1: Validate at a single point
print("\n1. Single Point Validation")
print("-" * 70)

# Reference conditions
p = 101325.0  # Pa (1 bar)
d = 0.01  # m (1 cm)
T = 300.0  # K

models = [
    ("PaschenSimple", PaschenSimpleModel()),
    ("PaschenTempCorrected", PaschenTemperatureCorrectedModel()),
]

for name, model in models:
    prob = om.Problem()
    prob.model.add_subsystem("breakdown", model, promotes=["*"])
    prob.setup()

    prob.set_val("gas_properties_pressure", p)
    prob.set_val("gap_distance", d)
    prob.set_val("preheat_temperature", T)

    prob.run_model()

    V_breakdown = prob.get_val("breakdown_voltage")[0]
    print(f"{name:25s}: {V_breakdown:8.1f} V")

# Example 2: Compare with experimental Paschen curve
print("\n2. Paschen Curve Comparison")
print("-" * 70)

pd_exp, V_exp, _ = get_paschen_curve_air()

print(f"Experimental data points: {len(pd_exp)}")
print(f"pd range: {pd_exp[0]:.2f} to {pd_exp[-1]:.0f} Torr·cm")
print(f"V range:  {V_exp[0]:.0f} to {V_exp[-1]:.0f} V")
print(f"Paschen minimum: {np.min(V_exp):.0f} V at pd = {pd_exp[np.argmin(V_exp)]:.2f} Torr·cm")

# Example 3: Spark breakdown transition
print("\n3. Spark Breakdown Transition (G-S)")
print("-" * 70)

pulses, field, error, dc_field = get_gs_transition_data()

print(f"Spark breakdown data points: {len(pulses)}")
print(f"Single-pulse field: {field[0]:.1f} ± {error[0]:.1f} kV/cm")
print(f"DC breakdown field: {dc_field:.1f} kV/cm")
print(f"Field reduction: {(field[0] - dc_field):.1f} kV/cm ({(field[0] / dc_field):.1f}x)")

# Example 4: Test RepetitivePulseBreakdownModel
print("\n4. Repetitive Pulse Breakdown Model")
print("-" * 70)

prob = om.Problem()
model = RepetitivePulseBreakdownModel()
prob.model.add_subsystem("breakdown", model, promotes=["*"])
prob.setup()

# Test at different pulse conditions
conditions = [
    {"f": 100.0, "t_res": 0.001, "beta": 1.0, "desc": "Low freq, no enhancement"},
    {"f": 1000.0, "t_res": 0.01, "beta": 3.0, "desc": "High freq, field enhancement"},
]

for cond in conditions:
    prob.set_val("gas_properties_pressure", 101325.0)
    prob.set_val("gap_distance", 0.01)
    prob.set_val("preheat_temperature", 300.0)
    prob.set_val("pulse_frequency", cond["f"])
    prob.set_val("pulse_duration", 1e-6)
    prob.set_val("residence_time", cond["t_res"])
    prob.set_val("field_enhancement_factor", cond["beta"])

    prob.run_model()

    V = prob.get_val("breakdown_voltage")[0]
    E = V / (0.01 * 100)  # kV/cm
    N_pulses = cond["f"] * cond["t_res"]

    print(f"\n{cond['desc']}:")
    print(f"  Frequency: {cond['f']:.0f} Hz")
    print(f"  Pulses/molecule: {N_pulses:.1f}")
    print(f"  Field enhancement: β = {cond['beta']:.1f}")
    print(f"  Breakdown field: {E:.2f} kV/cm")

# Example 5: Run full validation suite
print("\n5. Run Full Validation Suite")
print("-" * 70)
print("\nTo run the complete validation with all plots:")
print("  python -m paroto.validation.validate_breakdown_models")
print("\nThis will generate:")
print("  - paschen_curve_validation.png")
print("  - temperature_dependence_validation.png")
print("  - spark_breakdown_transition_validation.png")
print("  - model_comparison_matrix.png")

print("\n" + "=" * 70)
print("Example complete! See paroto/validation/README.md for details.")
print("=" * 70)